<br><br>
<div dir="rtl">



## نمذجة إمكانية الوصول إلى مداخل محطات المترو في الرياض باستخدام بيانات OpenStreetMap

<br>

**المقدمة**
<br><br>

بإذن الله سنركز على كيفية استخراج بيانات شبكة النقل العام في مدينة الرياض من [OpenStreetMap](https://www.openstreetmap.org/#map=11/24.7506/46.7472) باستخدام مكتبة [OSMnx](https://github.com/gboeing/osmnx-examples?tab=readme-ov-file) وذلك لاستخراج مواقع بوابات محطات المترو.


<br>

<br>

**الاهداف:**

- استخراج مداخل محطات المترو بمدينة الرياض من خلال بيانات OpenStreetMap.<br>

- بناء شبكة طرق للمشي باستخدام مكتبة OSMnx.
لحساب مناطق الخدمة (Isochrones) حول مداخل المترو لمسافة زمنية معينة (٥، ١٠، و١٥ دقائق مشي).

- تحميل شبكة الطرق لمدينة الرياض كملف Shapefile للاستفادة منه في أنظمة المعلومات الجغرافية (GIS).

<br><br>

  **ملاحظة:** <br>
البيانات الموجودة في OSM تعتمد على ادخالات المستخدمين فهي ليست كاملة. ومع ذلك، فهي قد تمثل نقطة انطلاق ممتازة لجلب البيانات الجغرافية وتحليلها خاصة  ان بيانات البوابات غير متوفرة بشكل رسمي.

<br><br>

In [1]:
# ───────────────────────────────────────────────────────────────
#  تحميل المكتبات
# ───────────────────────────────────────────────────────────────


%%capture
!pip install osmnx geopandas folium ipywidgets shapely

import os
import numpy as np
import pandas as pd
import geopandas as gpd
import osmnx as ox
import folium
import zipfile
import networkx as nx
import ipywidgets as widgets

from shapely.geometry import box, mapping, Point
from shapely import union_all
from shapely.ops import unary_union
from IPython.display import display
from tqdm.notebook import tqdm
from google.colab import files
import requests


In [2]:
# ───────────────────────────────────────────────────────────────
#  تحديد منطقة الدراسة لتحميل البيانات
# ───────────────────────────────────────────────────────────────


north, south, east, west = 25.00, 24.45, 47.00, 46.50

n_tiles = 3
lat_steps = np.linspace(south, north, n_tiles + 1)
lon_steps = np.linspace(west, east, n_tiles + 1)

tiles = []
for i in range(n_tiles):
    for j in range(n_tiles):
        n = lat_steps[i + 1]
        s = lat_steps[i]
        e = lon_steps[j + 1]
        w = lon_steps[j]
        tiles.append(box(w, s, e, n))



bbox_union = union_all(tiles)

center = [bbox_union.centroid.y, bbox_union.centroid.x]

# Create the base map
m = folium.Map(location=center, zoom_start=10.3, width=750, tiles="CartoDB Positron")

# Draw each tile as a rectangle on the map
for tile in tiles:
    gj = folium.GeoJson(mapping(tile), style_function=lambda x: {
        "fill": False,
        "color": "blue",
        "weight": 1
    })
    gj.add_to(m)

# Display the map
m

<br><br>
<div dir="rtl">


# **هنا تم تقسيم منطقة الدراسة إلى اكثر من منطقة لتسريع عملية تحميل البيانات**

<br><br>

In [3]:
# ───────────────────────────────────────────────────────────────
#  استخراج محطات المترو ومداخلها
# ───────────────────────────────────────────────────────────────

tags = {
    "railway": ["station", "subway_entrance"],

    "public_transport": ["platform", "stop_position"]
}

gdfs = []

with tqdm(total=len(tiles), desc="Downloading OSM features", unit="tile") as pbar:
    for idx, tile_poly in enumerate(tiles):
        try:
            gdf_tile = ox.features_from_polygon(tile_poly, tags=tags)
            gdfs.append(gdf_tile)
        except Exception as e:
            # print(f"❌  Failed tile {idx+1}: {e}")  ← suppress this
            pass
        pbar.update(1)


if gdfs:
    gdf_all = pd.concat(gdfs, ignore_index=True).set_geometry("geometry").set_crs(4326)
    print(f"\n✅ Total OSM features collected: {len(gdf_all)}")
else:
    gdf_all = gpd.GeoDataFrame(columns=["geometry"], crs=4326)
    print("⚠️ No OSM features were returned.")

stations_raw = gdf_all[(gdf_all["railway"] == "station") & (gdf_all["station"] == "subway")]
entrances    = gdf_all[gdf_all["railway"] == "subway_entrance"]
bus_raw      = gdf_all[
    (gdf_all["public_transport"].isin(["platform", "stop_position"]))
]

print(f"\n🟩 محطات المترو (stations): {len(stations_raw)}")
print(f"🟦 مداخل المترو (entrances): {len(entrances)}")


✅ Total OSM features collected: 847

🟩 محطات المترو (stations): 89
🟦 مداخل المترو (entrances): 256


<br><br>
<div dir="rtl">

# عدد مداخل المترو 256  الموجودة في موقع OSM   و عدد المحطات 89 بسبب وجود محطات مشتركة فالعدد الكلي حسب [المصادر الرسمية](https://opendata.rcrc.gov.sa/explore/dataset/metro-stations-in-riyadh-by-metro-line-and-station-type-2024/map/?disjunctive.metrostationnamear&disjunctive.metroline&disjunctive.mstationtypenamear&disjunctive.metrostationcode&location=10,24.76137,46.70186&basemap=jawg.streets) 85.

<br><br>

In [4]:
# ───────────────────────────────────────────────────────────────
#  عرض البيانات في خريطة باستخدام مكتبة
#Foliom
# ───────────────────────────────────────────────────────────────



def pointify(gdf):
    gdf = gdf.copy()
    gdf["geometry"] = gdf["geometry"].apply(
        lambda g: g.centroid if g.geom_type != "Point" else g
    )
    return gpd.GeoDataFrame(gdf, geometry="geometry", crs="EPSG:4326")


stations_all = gdf_all[(gdf_all["railway"] == "station") & (gdf_all["station"] == "subway")]
entrances     = gdf_all[gdf_all["railway"] == "subway_entrance"]


stn_map = pointify(stations_all)
ent_map = pointify(entrances)


minx, miny, maxx, maxy = stn_map.total_bounds
centre = [(miny + maxy) / 2, (minx + maxx) / 2]

m = folium.Map(location=centre, zoom_start=11, width=750, tiles="CartoDB Positron")
style = dict(radius=5, fill=True, fill_opacity=0.85, weight=0)


fg_stn = folium.FeatureGroup(name="محطات المترو", show=True).add_to(m)
fg_ent = folium.FeatureGroup(name="مداخل المترو", show=True).add_to(m)


for _, r in stn_map.iterrows():
    pt = r.geometry
    folium.CircleMarker([pt.y, pt.x], color="#3B5AFE", fill_color="#3B5AFE", **style,
                        tooltip=r.get("name", "محطة مترو")).add_to(fg_stn)


for _, r in ent_map.iterrows():
    pt = r.geometry
    folium.CircleMarker([pt.y, pt.x], color="#FF8F00", fill_color="#FF8F00", **style,
                        tooltip=r.get("name", "مدخل مترو")).add_to(fg_ent)


folium.LayerControl(collapsed=False).add_to(m)


legend = """
<div style="position: fixed; bottom: 50px; left: 50px; width: 150px; height: 60px;
            border:2px solid grey; z-index:9999; font-size:14px;
            background-color: white; padding: 10px;">
<span style="background:#3B5AFE;border-radius:50%;display:inline-block;width:10px;height:10px;"></span>
&nbsp;محطات المترو<br>
<span style="background:#FF8F00;border-radius:50%;display:inline-block;width:10px;height:10px;"></span>
&nbsp;مداخل المترو<br>
</div>
"""
m.get_root().html.add_child(folium.Element(legend))

m

In [ ]:
# ───────────────────────────────────────────────────────────────
#  تحميل الطبقات بصيغة
# Shapefile
# ───────────────────────────────────────────────────────────────


import warnings
warnings.filterwarnings("ignore")


def to_point_gdf(df):
    gdf = gpd.GeoDataFrame(df.copy(), geometry="geometry", crs="EPSG:4326")
    gdf["geometry"] = gdf["geometry"].apply(lambda g: g.centroid if g.geom_type != "Point" else g)
    return gdf



def to_zipped_shp(df, base):
    gdf = to_point_gdf(df).reset_index(drop=True)
    folder = f"/content/{base}"
    os.makedirs(folder, exist_ok=True)
    gdf.to_file(f"{folder}/{base}.shp")
    zip_path = f"/content/{base}.zip"
    with zipfile.ZipFile(zip_path, "w", zipfile.ZIP_DEFLATED) as zf:
        for file in os.listdir(folder):
            zf.write(os.path.join(folder, file), arcname=file)
    return zip_path


zip_stn = to_zipped_shp(stn_map, "riyadh_subway_stations")
zip_ent = to_zipped_shp(ent_map, "riyadh_subway_entrances")

def dl(label, path):
    b = widgets.Button(description=label, button_style="success", icon="download")
    b.on_click(lambda _: files.download(path))
    return b

display(widgets.HBox([
    dl("تحميل محطات المترو",  zip_stn),
    dl("تحميل مداخل المترو",  zip_ent)
]))


<br><br>
<div dir="rtl">

## تحميل شبكة المشي في الرياض
  
تشمل الشبكة المسارات التي يمكن استخدامها سيرًا على الأقدام، مثل الأرصفة والممرات الخاصة بالمشاة وبعض الشوارع المحلية التي تم تحديدها من قبل المساهمين في OpenStreetMap بقابلية المشي.  

يمكن تحميل هذه الشبكة كملف Shapefile لاستخدامه في تحليلات نظم المعلومات الجغرافية (GIS) .

<br>

قد يستغرق بعض الوقت (٥-٧ دقائق) لتحميل الشبكة بسبب حجم البيانات.

<br><br>

In [6]:
# ───────────────────────────────────────────────────────────────
#   تحميل شبكة طرق المشي بصيغة
# Shapefile
# ───────────────────────────────────────────────────────────────


graphs = []
with tqdm(total=len(tiles),  unit="tile") as pbar:
    for idx, tile_poly in enumerate(tiles):
        try:
            G_tile = ox.graph_from_polygon(tile_poly)
            graphs.append(G_tile)
        except Exception as e:
            print(f"❌ Failed tile {idx+1}: {e}")
        pbar.update(1)

G_walk = nx.compose_all(graphs)
print(f"✅ Network graph built with {len(G_walk.nodes)} nodes and {len(G_walk.edges)} edges.")


nodes, edges = ox.graph_to_gdfs(G_walk)


def to_zipped_shp_edges(edges_gdf, base):
    gdf = edges_gdf.reset_index(drop=True)
    folder = f"/content/{base}"
    os.makedirs(folder, exist_ok=True)
    gdf.to_file(f"{folder}/{base}.shp")
    zip_path = f"/content/{base}.zip"
    with zipfile.ZipFile(zip_path, "w", zipfile.ZIP_DEFLATED) as zf:
        for file in os.listdir(folder):
            zf.write(os.path.join(folder, file), arcname=file)
    return zip_path


zip_walk = to_zipped_shp_edges(edges, "riyadh_walk_network")


def dl(label, path):
    b = widgets.Button(description=label, button_style="success", icon="download")
    b.on_click(lambda _: files.download(path))
    return b

display(widgets.HBox([
    dl("تحميل شبكة المشي", zip_walk)
]))

  0%|          | 0/9 [00:00<?, ?tile/s]

✅ Network graph built with 184614 nodes and 470623 edges.


<br><br>
<div dir="rtl">


## حساب مناطق الخدمة لمداخل محطات المترو

في هذه الخطوة، سنقوم بحساب "مناطق الخدمة" الزمنية حول كل مدخل لمحطة المترو.  

<br>

يتم تنفيذ ذلك من خلال:
- إسقاط مداخل المترو إلى نفس نظام الإحداثيات المستخدم في شبكة المشي.
- ربط كل مدخل بأقرب عقدة في الشبكة.
- بناء شبكات فرعية (Ego Graphs) تمثل المسافة الممكنة حسب الزمن المحدد.
- تحويل الشبكات الفرعية إلى مضلعات تمثل المناطق الممكن الوصول إليها مشيًا في الفترة الزمنية.


<br><br>
### لماذا نقوم بحساب مناطق الخدمة حول **مداخل** المحطات وليس المحطات نفسها؟
<br>
غالبًا ما تمتد محطات المترو على مساحة كبيرة وقد تحتوي على عدة مداخل موزعة في مواقع مختلفة.

حساب منطقة الخدمة بناءً على موقع المحطة فقط يعطي نتائج غير دقيقة لأنه يتجاهل المسار الفعلي الذي يسلكه المشاة.

أما حساب منطقة الخدمة لكل **مدخل** فيعكس بشكل أدق واقع الوصول للمشاة، ويأخذ في الاعتبار:

<br>

- الموقع الحقيقي الذي يدخل منه الراكب إلى المحطة.
- توزيع المداخل حول المحطة الواحدة.
- تأثير تصميم المحطة وشبكة الطرق المحيطة على إمكانية الوصول.

<br>

لذلك فإن الاعتماد على **مداخل المترو** يوفر تحليلًا أكثر دقة وواقعية لإمكانية الوصول للمشاة.




In [ ]:

walk_speed = 1.3  # متر في الثانية
meters_per_minute = walk_speed * 60
times = [5, 10, 15]  # بالدقائق
ranges = [t * meters_per_minute for t in times]
colors = {5: "#66BB6A", 10: "#FFA726", 15: "#EF5350"}
labels_ar = {5: "٥ دقائق مشي", 10: "١٠ دقائق مشي", 15: "١٥ دقائق مشي"}


ent_proj = ent_map.to_crs(G_walk.graph['crs']).copy()


ent_proj["nearest_node"] = ox.distance.nearest_nodes(
    G_walk,
    X=ent_proj.geometry.x.values,
    Y=ent_proj.geometry.y.values
)



def build_isochrones(gdf, label):
    individual_polygons = []  
    merged_results = []       

    for _, row in tqdm(gdf.iterrows(), total=len(gdf), desc=f"⏱️ {label}"):
        node = row["nearest_node"]
        for dist_m in ranges:
            subgraph = nx.ego_graph(G_walk, node, radius=dist_m, distance="length")
            if not subgraph.edges:
                continue
            edges = ox.graph_to_gdfs(subgraph, nodes=False, edges=True)
            polygon = unary_union(edges.geometry).convex_hull

            
            individual_polygons.append({
                "geometry": polygon,
                "time_min": int(dist_m / meters_per_minute)
            })

   
    gdf_individual = gpd.GeoDataFrame(individual_polygons, crs=G_walk.graph['crs'])

   
    for t in times:
        polys = gdf_individual[gdf_individual["time_min"] == t]
        if not polys.empty:
            merged = unary_union(polys.geometry)
            merged_results.append({
                "geometry": merged,
                "time_min": t
            })

    gdf_merged = gpd.GeoDataFrame(merged_results, crs=G_walk.graph['crs'])
    return gdf_individual, gdf_merged


iso_ent_raw, iso_ent = build_isochrones(ent_proj, "مدخل مترو")

⏱️ مدخل مترو:   0%|          | 0/256 [00:00<?, ?it/s]

<br><br>
<div dir="rtl">


## سرعة المشي المستخدمة في التحليل

هنا تم افتراض أن سرعة المشي تساوي **١.٣ متر في الثانية**، وهي سرعة متوسطة تُستخدم كثيرًا في دراسات إمكانية الوصول الحضري و تعادل هذه السرعة تقريبًا **٧٨ مترًا في الدقيقة**.
بالإمكان تعديل على السرعة المستخدمة من خلال تعديل القيمة المدخلة هنا:

"walk_speed = 1.3 "
<br><br>


تم استخدام هذه السرعة لتحويل فترات الزمن (مثل ٥ أو ١٠ دقائق مشيًا) إلى مسافات فعلية يمكن الوصول إليها داخل شبكة الطرق، وتم بناء مناطق الخدمة بناءً على هذه القيم.

<br><br>

وفي الخلية التالية سيتم عرض مناطق الخدمة في خريطة المدينة.


In [ ]:

iso_raw_wgs = iso_ent_raw.to_crs("EPSG:4326")
m_raw = folium.Map(location=centre, zoom_start=12, tiles="CartoDB Positron")


fg_5 = folium.FeatureGroup(name="٥ دقائق مشي", show=True).add_to(m_raw)
fg_10 = folium.FeatureGroup(name="١٠ دقائق مشي", show=True).add_to(m_raw)
fg_15 = folium.FeatureGroup(name="١٥ دقائق مشي", show=True).add_to(m_raw)


fg_ent = folium.FeatureGroup(name="مداخل المترو", show=True).add_to(m_raw)


for _, row in iso_raw_wgs.iterrows():
    time = row["time_min"]
    color = colors.get(time, "#999999")
    gj = folium.GeoJson(
        row["geometry"],
        style_function=lambda _, color=color: {
            "fillColor": color,
            "color": color,
            "fillOpacity": 0.3,
            "weight": 0.5
        },
        tooltip=f"منطقة فردية – {labels_ar[time]}"
    )
    if time == 5:
        gj.add_to(fg_5)
    elif time == 10:
        gj.add_to(fg_10)
    elif time == 15:
        gj.add_to(fg_15)


for _, r in ent_map.iterrows():
    folium.CircleMarker(
        [r.geometry.y, r.geometry.x],
        radius=4,
        color="#000",
        fill=True,
        fill_color="#000",
        fill_opacity=1,
        tooltip=r.get("name", "مدخل مترو")
    ).add_to(fg_ent)


folium.LayerControl(collapsed=False).add_to(m_raw)


legend_html = """
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 180px;
    height: 110px;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
    background-color: white;
    padding: 10px;
">
<b>المدة الزمنية:</b><br>
<span style="background:#66BB6A;border-radius:50%;display:inline-block;width:10px;height:10px;"></span>
&nbsp;٥ دقائق<br>
<span style="background:#FFA726;border-radius:50%;display:inline-block;width:10px;height:10px;"></span>
&nbsp;١٠ دقائق<br>
<span style="background:#EF5350;border-radius:50%;display:inline-block;width:10px;height:10px;"></span>
&nbsp;١٥ دقائق
</div>
"""
m_raw.get_root().html.add_child(folium.Element(legend_html))


m_raw

<br><br>
<div dir="rtl">


## مقارنة بين مناطق الخدمة قبل وبعد دمج المناطق المتقاطعة


- **المضلعات الفردية**: كل مضلع يمثل منطقة خدمة لمدخل واحد من مداخل المترو.

- **المضلعات المدمجة**: يتم دمج جميع المضلعات التي تمثل نفس الفترة الزمنية في مضلع واحد لتبسيط العرض.

<br><br>
بشكل عام الدمج يساعد في إزالة التداخلات بين مناطق الخدمة وتقديم رؤية أوضح لنطاق الوصول الفعلي لكل زمن بحيث المداخل القريبة من بعضها تشترك في منطقة خدمة واحدة.

In [ ]:

centre = [ent_map.geometry.y.mean(), ent_map.geometry.x.mean()]
m_iso = folium.Map(location=centre, zoom_start=12, tiles="CartoDB Positron")
style = dict(fillOpacity=0.4, weight=1)


fg_5 = folium.FeatureGroup(name="٥ دقائق مشي", show=True).add_to(m_iso)
fg_10 = folium.FeatureGroup(name="١٠ دقائق مشي", show=True).add_to(m_iso)
fg_15 = folium.FeatureGroup(name="١٥ دقائق مشي", show=True).add_to(m_iso)
fg_ent = folium.FeatureGroup(name="مداخل المترو", show=True).add_to(m_iso)


iso_ent_wgs = iso_ent.to_crs("EPSG:4326")


for _, row in iso_ent_wgs.iterrows():
    time = row["time_min"]
    color = colors.get(time, "#999999")
    tooltip = labels_ar[time]
    gj = folium.GeoJson(
        row["geometry"],
        style_function=lambda _, color=color: {
            "fillColor": color,
            "color": color,
            "fillOpacity": 0.4,
            "weight": 1
        },
        tooltip=tooltip
    )
    if time == 5:
        gj.add_to(fg_5)
    elif time == 10:
        gj.add_to(fg_10)
    elif time == 15:
        gj.add_to(fg_15)


for _, r in ent_map.iterrows():
    folium.CircleMarker(
        [r.geometry.y, r.geometry.x],
        radius=4,
        color="#000",
        fill=True,
        fill_color="#000",
        fill_opacity=1,
        tooltip=r.get("name", "مدخل مترو")
    ).add_to(fg_ent)


folium.LayerControl(collapsed=False).add_to(m_iso)


legend_html = """
<div style="
    position: fixed;
    bottom: 50px;
    left: 50px;
    width: 180px;
    height: 110px;
    border:2px solid grey;
    z-index:9999;
    font-size:14px;
    background-color: white;
    padding: 10px;
">
<b>المدة الزمنية:</b><br>
<span style="background:#66BB6A;border-radius:50%;display:inline-block;width:10px;height:10px;"></span>
&nbsp;٥ دقائق<br>
<span style="background:#FFA726;border-radius:50%;display:inline-block;width:10px;height:10px;"></span>
&nbsp;١٠ دقائق<br>
<span style="background:#EF5350;border-radius:50%;display:inline-block;width:10px;height:10px;"></span>
&nbsp;١٥ دقائق
</div>
"""
m_iso.get_root().html.add_child(folium.Element(legend_html))


m_iso



<br><br>
<div dir="rtl">


# **لتحميل مناطق الخدمة بصيغة Shapefile.**

<br><br>


In [10]:

def to_zipped_shp(df, base):
    gdf = df.reset_index(drop=True)
    folder = f"/content/{base}"
    os.makedirs(folder, exist_ok=True)
    gdf.to_file(f"{folder}/{base}.shp")
    zip_path = f"/content/{base}.zip"
    with zipfile.ZipFile(zip_path, "w", zipfile.ZIP_DEFLATED) as zf:
        for file in os.listdir(folder):
            zf.write(os.path.join(folder, file), arcname=file)
    return zip_path


zip_iso = to_zipped_shp(iso_ent, "riyadh_walk_isochrones")


def dl(label, path):
    b = widgets.Button(description=label, button_style="success", icon="download")
    b.on_click(lambda _: files.download(path))
    return b


display(dl("تحميل مناطق الخدمة", zip_iso))

Button(button_style='success', description='تحميل مناطق الخدمة', icon='download', style=ButtonStyle())

<br><br>
<div dir="rtl">



**بالإمكان تطوير هذا الشرح بإضافة بيانات محطات الباصات من موقع [البيانات المفتوحة](https://opendata.rcrc.gov.sa/explore/dataset/bus-stops-in-riyadh-by-bus-route-direction-and-shelter-type-2024/export/?disjunctive.busstopnamear&disjunctive.bsheltertypear&disjunctive.pubtransstagear&location=10,24.6737,46.72469&basemap=jawg.streets) الخاص بالهيئة الملكية لمدينة الرياض.**

**بسبب ان موقع OSM  لا يحتوي على عدد كبير منها وليس هناك فرق بين البوابة وموقع المحطة نفسها.**

<br><br>


In [11]:


url = "https://raw.githubusercontent.com/Malmusidi/riyadh-data/main/data/bus-stops-in-riyadh-by-bus-route-direction-and-shelter-type-2024.json"
response = requests.get(url)
data = response.json()

df = pd.json_normalize(data)
df["geometry"] = df.apply(lambda row: Point(row["geo_point_2d.lon"], row["geo_point_2d.lat"]), axis=1)
gdf = gpd.GeoDataFrame(df, geometry="geometry", crs="EPSG:4326")


print(f"🟧 مواقف الحافلات (bus stops): {len(df)}")


🟧 مواقف الحافلات (bus stops): 3010


In [12]:



center = [gdf.geometry.y.mean(), gdf.geometry.x.mean()]
m = folium.Map(location=center, zoom_start=11, tiles="CartoDB Positron")


for i, row in gdf.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=3,
        color="red",
        fill=True,
        fill_opacity=0.8,
        tooltip=f"Stop #{i+1} | Route: {row.get('busroute')} | Dir: {row.get('direction')}"
    ).add_to(m)

m

<br><br>
<div dir="rtl">


## الخاتمة

في هذا الشرح تم تطبيق خطوات عملية لنمذجة إمكانية الوصول إلى مداخل محطات المترو في مدينة الرياض باستخدام بيانات OpenStreetMap ومكتبة OSMnx.

تعرفنا على كيفية:
- تحميل شبكة المشي وبناؤها من خلال تقسيم منطقة الدراسة.

- استخراج مداخل المترو وربطها بالشبكة.

- حساب مناطق الخدمة الزمنية (٥، ١٠، ١٥ دقائق مشيًا) حول كل مدخل.

- مقارنة المخرجات قبل وبعد دمج المضلعات المتداخلة.

- حفظ النتائج وتحميلها بصيغ قابلة للاستخدام في أنظمة المعلومات الجغرافية (Shapefile).

<br><br>

في الختام، هذا النوع من التحليل يُعد أداة في دراسات إمكانية الوصول والتخطيط الحضري، ويساعد في فهم واقع تنقل المشاة ومدى تغطية النقل العام.


وبالله التوفيق،


